# Assignment 1: Information Retrieval (10 marks)

This assignment is based on the Assignment 1 Demo tutorials.

In this assignment, your task is to index a new document collection into *Elasticsearch*, and then measure search performance based on predefined queries.

A new document collection containing more than 10,000 goverment sites description, and a set of predefined queries, is provided for this assignment.

Throughout this assginment: 
1. You will develop a better understanding of indexing, including the tokeniser, parser, and normaliser components, and how to improve the search performance given a predefined evaluation metric, 
2. You will develop a better understanding of search algorithms, and how to obtain better search results, and 
3. You will find the best way to combine an indexer and search algorithm to maximise your performance.

Below, you will solve five programming questions, and three written questions. 

We will check the correctness of your code and the overall performance score.

- Write your code after `### Your code here`, and remove `raise NotImplementedError` after implementation.
- Write answers in this notebook file in the designated cells, and upload the file to the Wattle submission site. **Please rename and submit jupyter notebook file (`Assignment1.ipynb`) to `your_uid.ipynb` (e.g. `u1234567.ipynb`) with your written answers therein - FAILURE TO DO SO WILL RESULT IN -0.5 POINTS**. 

*Hint*: After finishing coding your notebook, select from the Jupyter Notebook interface the menu option Kernel -> Restart & Run All. After the execution of each block is finished, inspect the output, save the notebook and shutdown the kernel. Only now you can safely manipulate the .ipynb file, which contains code, explanations and output.

## Coding component (Q1 - Q5), 4 marks

### Q1: Index Gov dataset (0.5 marks)

For this assignment we will be working with a corpus of government documents, located in the gov folder. 

The gov folder contains three sub-folders; documents, qrels and topics. The documents folder consists of sub-folders, each of which contain multiple documents. Topics and qrels contain search queries and corresponding ground truth relevant documents, respectively.

Your first job is to index the documents as we have done in the tutorial exercises (Assignment 1 Demo).

Note that depending on your machine, indexing may take several minutes to a few hours. You may implement multi-threaded version of indexing to mitigate this problem.

Below is provided the basic code configuration for indexing:

In [3]:
# basic configuration for indexing
basic_settings = {
  "mappings": {
    "doc": {
      "properties": {
        "filename": {
          "type": "keyword",
          "index": False,
        },
        "path": {
          "type": "keyword",
          "index": False,
        },
        "text": {
          "type": "text",
          "similarity": "boolean",
          "analyzer": "my_analyzer",
          "search_analyzer": "my_analyzer"
        }
      }
    }
  },
  "settings": {
    "analysis": {
      "analyzer": {
        "my_analyzer": {
          "filter": [
            "stop"
          ],
          "char_filter": [
            "html_strip"
          ],
          "type": "custom",
          "tokenizer": "whitespace"
        }
      }
    }
  }   
}

You need to implement the below function `build_gov_index`. Don't forget to remove `raise NotImplementedError` after implementation.

In [4]:
from elasticsearch import Elasticsearch
import os
from collections import namedtuple

ES_HOSTS = ['http://localhost:9200']
DOCS_PATH = 'E:\Comp 4650\Assignment_1\Assignment_1\gov\documents'
INDEX_NAME = 'gov'
DOC_TYPE = 'doc'

Doc = namedtuple('Doc', 'filename path text')

def read_doc(doc_path, encoding):
    '''
        reads a document from path
        input:
            - doc_path : path of document
            - encoding: encoding
        output: =>
            - doc: instance of Doc namedtuple
    '''
    filename = doc_path.split('/')[-1]
    fp = open(doc_path, 'r', encoding = encoding)
    text = fp.read().strip()
    fp.close()
    return Doc(filename = filename, text = text, path = doc_path)


def read_dataset(path, encoding = "ISO-8859-1"):
    '''
        reads multiple documents from path
        input:
            - doc_path : path of document
            - encoding: encoding
        output: =>
            - docs: instances of Doc namedtuple returned as generator
    '''
    for root, dirs, files in os.walk(path):
        for doc_path in files:
            yield read_doc(root + '/' + doc_path, encoding)

def build_gov_index(es_conn, index_name, doc_path, settings):
    # TODO implement function that:
    #  1. Create an index with `index_name`. If `index_name` already exists, remove the index first.
    #  2. Index the documents under doc_path, including subfolders, into elasticsearch (hint: read demo carefully)
    # Note that this function will be used throughout this assignment    
    # YOUR CODE HERE
    if es_conn.indices.exists(index_name):
        es_conn.indices.delete(index = index_name)
        print('index `{}` deleted'.format(index_name))
    es_conn.indices.create(index = index_name, ignore = 400, body = settings)
    print('index `{}` created'.format(index_name))

    counter_read, counter_idx_failed = 0, 0 # counters
    
    # retrive & index documents
    dataset = read_dataset(doc_path)
    for doc in dataset:
        res = es_conn.index(
            index = index_name,
            id = doc.filename,
            doc_type = DOC_TYPE,
            body = doc._asdict())
        counter_read += 1

        if res['result'] != 'created':
            conter_idx_failed += 1
        else:
            print('indexed {} documents'.format(counter_read))

    print('indexed {} docs to index `{}`, failed to index {} docs'.format(
        counter_read,
        index_name,
        counter_idx_failed
    ))
    
    # refresh after indexing
    es_conn.indices.refresh(index=index_name) 
    #run query

es_conn = Elasticsearch(ES_HOSTS)
build_gov_index(es_conn, INDEX_NAME, DOCS_PATH, basic_settings)

index `gov` deleted
index `gov` created
indexed 1 documents
indexed 2 documents
indexed 3 documents
indexed 4 documents
indexed 5 documents
indexed 6 documents
indexed 7 documents
indexed 8 documents
indexed 9 documents
indexed 10 documents
indexed 11 documents
indexed 12 documents
indexed 13 documents
indexed 14 documents
indexed 15 documents
indexed 16 documents
indexed 17 documents
indexed 18 documents
indexed 19 documents
indexed 20 documents
indexed 21 documents
indexed 22 documents
indexed 23 documents
indexed 24 documents
indexed 25 documents
indexed 26 documents
indexed 27 documents
indexed 28 documents
indexed 29 documents
indexed 30 documents
indexed 31 documents
indexed 32 documents
indexed 33 documents
indexed 34 documents
indexed 35 documents
indexed 36 documents
indexed 37 documents
indexed 38 documents
indexed 39 documents
indexed 40 documents
indexed 41 documents
indexed 42 documents
indexed 43 documents
indexed 44 documents
indexed 45 documents
indexed 46 documents
ind

indexed 379 documents
indexed 380 documents
indexed 381 documents
indexed 382 documents
indexed 383 documents
indexed 384 documents
indexed 385 documents
indexed 386 documents
indexed 387 documents
indexed 388 documents
indexed 389 documents
indexed 390 documents
indexed 391 documents
indexed 392 documents
indexed 393 documents
indexed 394 documents
indexed 395 documents
indexed 396 documents
indexed 397 documents
indexed 398 documents
indexed 399 documents
indexed 400 documents
indexed 401 documents
indexed 402 documents
indexed 403 documents
indexed 404 documents
indexed 405 documents
indexed 406 documents
indexed 407 documents
indexed 408 documents
indexed 409 documents
indexed 410 documents
indexed 411 documents
indexed 412 documents
indexed 413 documents
indexed 414 documents
indexed 415 documents
indexed 416 documents
indexed 417 documents
indexed 418 documents
indexed 419 documents
indexed 420 documents
indexed 421 documents
indexed 422 documents
indexed 423 documents
indexed 42

indexed 755 documents
indexed 756 documents
indexed 757 documents
indexed 758 documents
indexed 759 documents
indexed 760 documents
indexed 761 documents
indexed 762 documents
indexed 763 documents
indexed 764 documents
indexed 765 documents
indexed 766 documents
indexed 767 documents
indexed 768 documents
indexed 769 documents
indexed 770 documents
indexed 771 documents
indexed 772 documents
indexed 773 documents
indexed 774 documents
indexed 775 documents
indexed 776 documents
indexed 777 documents
indexed 778 documents
indexed 779 documents
indexed 780 documents
indexed 781 documents
indexed 782 documents
indexed 783 documents
indexed 784 documents
indexed 785 documents
indexed 786 documents
indexed 787 documents
indexed 788 documents
indexed 789 documents
indexed 790 documents
indexed 791 documents
indexed 792 documents
indexed 793 documents
indexed 794 documents
indexed 795 documents
indexed 796 documents
indexed 797 documents
indexed 798 documents
indexed 799 documents
indexed 80

indexed 1124 documents
indexed 1125 documents
indexed 1126 documents
indexed 1127 documents
indexed 1128 documents
indexed 1129 documents
indexed 1130 documents
indexed 1131 documents
indexed 1132 documents
indexed 1133 documents
indexed 1134 documents
indexed 1135 documents
indexed 1136 documents
indexed 1137 documents
indexed 1138 documents
indexed 1139 documents
indexed 1140 documents
indexed 1141 documents
indexed 1142 documents
indexed 1143 documents
indexed 1144 documents
indexed 1145 documents
indexed 1146 documents
indexed 1147 documents
indexed 1148 documents
indexed 1149 documents
indexed 1150 documents
indexed 1151 documents
indexed 1152 documents
indexed 1153 documents
indexed 1154 documents
indexed 1155 documents
indexed 1156 documents
indexed 1157 documents
indexed 1158 documents
indexed 1159 documents
indexed 1160 documents
indexed 1161 documents
indexed 1162 documents
indexed 1163 documents
indexed 1164 documents
indexed 1165 documents
indexed 1166 documents
indexed 116

indexed 1482 documents
indexed 1483 documents
indexed 1484 documents
indexed 1485 documents
indexed 1486 documents
indexed 1487 documents
indexed 1488 documents
indexed 1489 documents
indexed 1490 documents
indexed 1491 documents
indexed 1492 documents
indexed 1493 documents
indexed 1494 documents
indexed 1495 documents
indexed 1496 documents
indexed 1497 documents
indexed 1498 documents
indexed 1499 documents
indexed 1500 documents
indexed 1501 documents
indexed 1502 documents
indexed 1503 documents
indexed 1504 documents
indexed 1505 documents
indexed 1506 documents
indexed 1507 documents
indexed 1508 documents
indexed 1509 documents
indexed 1510 documents
indexed 1511 documents
indexed 1512 documents
indexed 1513 documents
indexed 1514 documents
indexed 1515 documents
indexed 1516 documents
indexed 1517 documents
indexed 1518 documents
indexed 1519 documents
indexed 1520 documents
indexed 1521 documents
indexed 1522 documents
indexed 1523 documents
indexed 1524 documents
indexed 152

...

indexed 28923 documents
indexed 28924 documents
indexed 28925 documents
indexed 28926 documents
indexed 28927 documents
indexed 28928 documents
indexed 28929 documents
indexed 28930 documents
indexed 28931 documents
indexed 28932 documents
indexed 28933 documents
indexed 28934 documents
indexed 28935 documents
indexed 28936 documents
indexed 28937 documents
indexed 28938 documents
indexed 28939 documents
indexed 28940 documents
indexed 28941 documents
indexed 28942 documents
indexed 28943 documents
indexed 28944 documents
indexed 28945 documents
indexed 28946 documents
indexed 28947 documents
indexed 28948 documents
indexed 28949 documents
indexed 28950 documents
indexed 28951 documents
indexed 28952 documents
indexed 28953 documents
indexed 28954 documents
indexed 28955 documents
indexed 28956 documents
indexed 28957 documents
indexed 28958 documents
indexed 28959 documents
indexed 28960 documents
indexed 28961 documents
indexed 28962 documents
indexed 28963 documents
indexed 28964 do

indexed 29265 documents
indexed 29266 documents
indexed 29267 documents
indexed 29268 documents
indexed 29269 documents
indexed 29270 documents
indexed 29271 documents
indexed 29272 documents
indexed 29273 documents
indexed 29274 documents
indexed 29275 documents
indexed 29276 documents
indexed 29277 documents
indexed 29278 documents
indexed 29279 documents
indexed 29280 documents
indexed 29281 documents
indexed 29282 documents
indexed 29283 documents
indexed 29284 documents
indexed 29285 documents
indexed 29286 documents
indexed 29287 documents
indexed 29288 documents
indexed 29289 documents
indexed 29290 documents
indexed 29291 documents
indexed 29292 documents
indexed 29293 documents
indexed 29294 documents
indexed 29295 documents
indexed 29296 documents
indexed 29297 documents
indexed 29298 documents
indexed 29299 documents
indexed 29300 documents
indexed 29301 documents
indexed 29302 documents
indexed 29303 documents
indexed 29304 documents
indexed 29305 documents
indexed 29306 do

indexed 29608 documents
indexed 29609 documents
indexed 29610 documents
indexed 29611 documents
indexed 29612 documents
indexed 29613 documents
indexed 29614 documents
indexed 29615 documents
indexed 29616 documents
indexed 29617 documents
indexed 29618 documents
indexed 29619 documents
indexed 29620 documents
indexed 29621 documents
indexed 29622 documents
indexed 29623 documents
indexed 29624 documents
indexed 29625 documents
indexed 29626 documents
indexed 29627 documents
indexed 29628 documents
indexed 29629 documents
indexed 29630 documents
indexed 29631 documents
indexed 29632 documents
indexed 29633 documents
indexed 29634 documents
indexed 29635 documents
indexed 29636 documents
indexed 29637 documents
indexed 29638 documents
indexed 29639 documents
indexed 29640 documents
indexed 29641 documents
indexed 29642 documents
indexed 29643 documents
indexed 29644 documents
indexed 29645 documents
indexed 29646 documents
indexed 29647 documents
indexed 29648 documents
indexed 29649 do

indexed 29951 documents
indexed 29952 documents
indexed 29953 documents
indexed 29954 documents
indexed 29955 documents
indexed 29956 documents
indexed 29957 documents
indexed 29958 documents
indexed 29959 documents
indexed 29960 documents
indexed 29961 documents
indexed 29962 documents
indexed 29963 documents
indexed 29964 documents
indexed 29965 documents
indexed 29966 documents
indexed 29967 documents
indexed 29968 documents
indexed 29969 documents
indexed 29970 documents
indexed 29971 documents
indexed 29972 documents
indexed 29973 documents
indexed 29974 documents
indexed 29975 documents
indexed 29976 documents
indexed 29977 documents
indexed 29978 documents
indexed 29979 documents
indexed 29980 documents
indexed 29981 documents
indexed 29982 documents
indexed 29983 documents
indexed 29984 documents
indexed 29985 documents
indexed 29986 documents
indexed 29987 documents
indexed 29988 documents
indexed 29989 documents
indexed 29990 documents
indexed 29991 documents
indexed 29992 do

ConnectionTimeout: ConnectionTimeout caused by - ReadTimeoutError(HTTPConnectionPool(host='localhost', port=9200): Read timed out. (read timeout=10))

### Q2: Search and performance measure (0.5 marks)

For this second task, you will first need to read the topics/gov.topics file. 

As we have done in the demo tutorial, each file is formatted as `query_id query_terms`, where
query_id is a numerical number, and query_terms consists of multiple keywords as search terms. 

Your job is to read the query file and search using the provided search function. You will need to write the output of the search results to an output.txt file in the trec-eval standard format used in the demo tutorial. 

As a reminder, this means that each result of each query should be put in a line in the output.txt like this:

`01 Q0 email09 0 1.23 my_IR_system1`

`01 Q0 email09 1 1.11 my_IR_system1`

`02 Q0 email07 0 1.08 my_IR_system1`

where '01' is the query ID; ignore 'Q0'; 'emailxx' is the name of the file; '0' (or '1' or some other integer number) is the rank of this result; '1.23' (or '1.08' or some other number) is the score of this result; and 'my_IR_system1' is the name for your retrieval system. 

Note that you are only allowed to write 10-documents at most for each query. If your output file contains more than 10 documents per query, you will get 0 score for this question.

**Please rename your output_q2.txt file to `YourUID_output_q2.txt` eg `u1234567_output_q2.txt`, before submitting to Wattle - FAILURE TO DO SO WILL RESULT IN -0.5 POINTS**.

Below is some code to get you started and for you to complete:

In [5]:
def search(query_string, es_conn, index_name):
    '''
        searches for query_string with default search algorithm
        input:
            - query_string: a query
            - es_conn: elasticsearch connection
            - index_name: name of index
        output:
            - a generator of tuple (filename, score)

    '''
    res = es_conn.search(index = index_name,
        body = {
            "_source": [ "filename"],
            "query": {
                "query_string": {
                    "query": query_string,
                }
            }
        }
    )
    return res['hits']['hits']
            
# TODO: 
#       Read query file from `query_path`, search using `search_fn`, and 
#       Write top 10 outputs per query to `output_file`
#       Note that the function takes a search function as an argument. You can directly call the search function
#       as `result = search_fn(query_string, es_conn, index_name)` within the function.
#       This function will be used throughout this assignment

#-- Reference - https://gist.github.com/lexingxie/4f294962084c013ba75b12ca6dd85fdc ----------------------------------
def read_search_write_output(search_fn, query_path, output_file):
    with open(query_path,'r') as f:
        with open(output_file ,'w') as output:
            for line in f:
                tokens = line.strip().split()
                search_terms = ' '.join(tokens[1:])
                cnt = 1
                result = search_fn(search_terms,es_conn,INDEX_NAME)
                for hit in result:
                    filename = hit["_source"]["filename"]
                    score = hit["_score"]
                    output.write('{} Q0 {} {} {} my_IR_system1\n'.format(tokens[0], filename, cnt, score))
                    cnt += 1
# ----------------------------------------------------------------------------------------------------------                   
query_path = 'E:\\Comp 4650\\Assignment_1\\Assignment_1\\gov\\topics\\gov.topics'
output_file = 'output.txt'
read_search_write_output(search, query_path, output_file)

Once you have written the results of your query to an output file, you can run trec-eval on your output file and the provided gov.qrel file to evaluate your system. Trec-eval provides many different measures of quality, but for the purposes of this assignment you will use precision@10 (p_10 in trec-eval output) to measure the performance of your systems.

In [6]:
!./trec_eval/trec_eval ./gov/qrels/gov.qrels output.txt

'.' is not recognized as an internal or external command,
operable program or batch file.


### Q3: Improving the search algorithm: compare similarity algorithms (1 mark)

*Elasticsearch* also provides multiple configurable scoring algorithms. 

For this task, you will be asked to find a better similarity module to improve the search performance. Please refer [here](https://www.elastic.co/guide/en/elasticsearch/reference/current/similarity.html) for a better understanding of the configurable elasticsearch similarity modules.

Here's some code to get you started and for you to complete:

In [9]:
# TODO: define your own analyzer for indexing and searching
q3_settings = {
  "mappings": {
    "doc": {
      "properties": {
        "filename": {
          "type": "keyword",
          "index": False,
        },
        "path": {
          "type": "keyword",
          "index": False,
        },
        "text": {
          "type": "text",
          "similarity": "BM25",
          "analyzer": "my_analyzer",
          "search_analyzer": "my_analyzer"
        }
      }
    }
  },
  "settings": {
    "analysis": {
      "analyzer": {
        "my_analyzer": {
          "filter": [
            "stop"
          ],
          "char_filter": [
            "html_strip"
          ],
          "type": "custom",
          "tokenizer": "whitespace"
        }
      }
    }
  }   
}
output_file1 = 'output1.txt'

In [10]:
# TODO: run this block to generate an output based on q3_settings defined above.
build_gov_index(es_conn, INDEX_NAME, DOCS_PATH, q3_settings)
read_search_write_output(search, query_path, output_file1)

index `gov` deleted
index `gov` created
indexed 1 documents
indexed 2 documents
indexed 3 documents
indexed 4 documents
indexed 5 documents
indexed 6 documents
indexed 7 documents
indexed 8 documents
indexed 9 documents
indexed 10 documents
indexed 11 documents
indexed 12 documents
indexed 13 documents
indexed 14 documents
indexed 15 documents
indexed 16 documents
indexed 17 documents
indexed 18 documents
indexed 19 documents
indexed 20 documents
indexed 21 documents
indexed 22 documents
indexed 23 documents
indexed 24 documents
indexed 25 documents
indexed 26 documents
indexed 27 documents
indexed 28 documents
indexed 29 documents
indexed 30 documents
indexed 31 documents
indexed 32 documents
indexed 33 documents
indexed 34 documents
indexed 35 documents
indexed 36 documents
indexed 37 documents
indexed 38 documents
indexed 39 documents
indexed 40 documents
indexed 41 documents
indexed 42 documents
indexed 43 documents
indexed 44 documents
indexed 45 documents
indexed 46 documents
ind

indexed 385 documents
indexed 386 documents
indexed 387 documents
indexed 388 documents
indexed 389 documents
indexed 390 documents
indexed 391 documents
indexed 392 documents
indexed 393 documents
indexed 394 documents
indexed 395 documents
indexed 396 documents
indexed 397 documents
indexed 398 documents
indexed 399 documents
indexed 400 documents
indexed 401 documents
indexed 402 documents
indexed 403 documents
indexed 404 documents
indexed 405 documents
indexed 406 documents
indexed 407 documents
indexed 408 documents
indexed 409 documents
indexed 410 documents
indexed 411 documents
indexed 412 documents
indexed 413 documents
indexed 414 documents
indexed 415 documents
indexed 416 documents
indexed 417 documents
indexed 418 documents
indexed 419 documents
indexed 420 documents
indexed 421 documents
indexed 422 documents
indexed 423 documents
indexed 424 documents
indexed 425 documents
indexed 426 documents
indexed 427 documents
indexed 428 documents
indexed 429 documents
indexed 43

indexed 764 documents
indexed 765 documents
indexed 766 documents
indexed 767 documents
indexed 768 documents
indexed 769 documents
indexed 770 documents
indexed 771 documents
indexed 772 documents
indexed 773 documents
indexed 774 documents
indexed 775 documents
indexed 776 documents
indexed 777 documents
indexed 778 documents
indexed 779 documents
indexed 780 documents
indexed 781 documents
indexed 782 documents
indexed 783 documents
indexed 784 documents
indexed 785 documents
indexed 786 documents
indexed 787 documents
indexed 788 documents
indexed 789 documents
indexed 790 documents
indexed 791 documents
indexed 792 documents
indexed 793 documents
indexed 794 documents
indexed 795 documents
indexed 796 documents
indexed 797 documents
indexed 798 documents
indexed 799 documents
indexed 800 documents
indexed 801 documents
indexed 802 documents
indexed 803 documents
indexed 804 documents
indexed 805 documents
indexed 806 documents
indexed 807 documents
indexed 808 documents
indexed 80

indexed 1133 documents
indexed 1134 documents
indexed 1135 documents
indexed 1136 documents
indexed 1137 documents
indexed 1138 documents
indexed 1139 documents
indexed 1140 documents
indexed 1141 documents
indexed 1142 documents
indexed 1143 documents
indexed 1144 documents
indexed 1145 documents
indexed 1146 documents
indexed 1147 documents
indexed 1148 documents
indexed 1149 documents
indexed 1150 documents
indexed 1151 documents
indexed 1152 documents
indexed 1153 documents
indexed 1154 documents
indexed 1155 documents
indexed 1156 documents
indexed 1157 documents
indexed 1158 documents
indexed 1159 documents
indexed 1160 documents
indexed 1161 documents
indexed 1162 documents
indexed 1163 documents
indexed 1164 documents
indexed 1165 documents
indexed 1166 documents
indexed 1167 documents
indexed 1168 documents
indexed 1169 documents
indexed 1170 documents
indexed 1171 documents
indexed 1172 documents
indexed 1173 documents
indexed 1174 documents
indexed 1175 documents
indexed 117

indexed 1491 documents
indexed 1492 documents
indexed 1493 documents
indexed 1494 documents
indexed 1495 documents
indexed 1496 documents
indexed 1497 documents
indexed 1498 documents
indexed 1499 documents
indexed 1500 documents
indexed 1501 documents
indexed 1502 documents
indexed 1503 documents
indexed 1504 documents
indexed 1505 documents
indexed 1506 documents
indexed 1507 documents
indexed 1508 documents
indexed 1509 documents
indexed 1510 documents
indexed 1511 documents
indexed 1512 documents
indexed 1513 documents
indexed 1514 documents
indexed 1515 documents
indexed 1516 documents
indexed 1517 documents
indexed 1518 documents
indexed 1519 documents
indexed 1520 documents
indexed 1521 documents
indexed 1522 documents
indexed 1523 documents
indexed 1524 documents
indexed 1525 documents
indexed 1526 documents
indexed 1527 documents
indexed 1528 documents
indexed 1529 documents
indexed 1530 documents
indexed 1531 documents
indexed 1532 documents
indexed 1533 documents
indexed 153

...

indexed 32379 documents
indexed 32380 documents
indexed 32381 documents
indexed 32382 documents
indexed 32383 documents
indexed 32384 documents
indexed 32385 documents
indexed 32386 documents
indexed 32387 documents
indexed 32388 documents
indexed 32389 documents
indexed 32390 documents
indexed 32391 documents
indexed 32392 documents
indexed 32393 documents
indexed 32394 documents
indexed 32395 documents
indexed 32396 documents
indexed 32397 documents
indexed 32398 documents
indexed 32399 documents
indexed 32400 documents
indexed 32401 documents
indexed 32402 documents
indexed 32403 documents
indexed 32404 documents
indexed 32405 documents
indexed 32406 documents
indexed 32407 documents
indexed 32408 documents
indexed 32409 documents
indexed 32410 documents
indexed 32411 documents
indexed 32412 documents
indexed 32413 documents
indexed 32414 documents
indexed 32415 documents
indexed 32416 documents
indexed 32417 documents
indexed 32418 documents
indexed 32419 documents
indexed 32420 do

indexed 32722 documents
indexed 32723 documents
indexed 32724 documents
indexed 32725 documents
indexed 32726 documents
indexed 32727 documents
indexed 32728 documents
indexed 32729 documents
indexed 32730 documents
indexed 32731 documents
indexed 32732 documents
indexed 32733 documents
indexed 32734 documents
indexed 32735 documents
indexed 32736 documents
indexed 32737 documents
indexed 32738 documents
indexed 32739 documents
indexed 32740 documents
indexed 32741 documents
indexed 32742 documents
indexed 32743 documents
indexed 32744 documents
indexed 32745 documents
indexed 32746 documents
indexed 32747 documents
indexed 32748 documents
indexed 32749 documents
indexed 32750 documents
indexed 32751 documents
indexed 32752 documents
indexed 32753 documents
indexed 32754 documents
indexed 32755 documents
indexed 32756 documents
indexed 32757 documents
indexed 32758 documents
indexed 32759 documents
indexed 32760 documents
indexed 32761 documents
indexed 32762 documents
indexed 32763 do

indexed 33066 documents
indexed 33067 documents
indexed 33068 documents
indexed 33069 documents
indexed 33070 documents
indexed 33071 documents
indexed 33072 documents
indexed 33073 documents
indexed 33074 documents
indexed 33075 documents
indexed 33076 documents
indexed 33077 documents
indexed 33078 documents
indexed 33079 documents
indexed 33080 documents
indexed 33081 documents
indexed 33082 documents
indexed 33083 documents
indexed 33084 documents
indexed 33085 documents
indexed 33086 documents
indexed 33087 documents
indexed 33088 documents
indexed 33089 documents
indexed 33090 documents
indexed 33091 documents
indexed 33092 documents
indexed 33093 documents
indexed 33094 documents
indexed 33095 documents
indexed 33096 documents
indexed 33097 documents
indexed 33098 documents
indexed 33099 documents
indexed 33100 documents
indexed 33101 documents
indexed 33102 documents
indexed 33103 documents
indexed 33104 documents
indexed 33105 documents
indexed 33106 documents
indexed 33107 do

indexed 33409 documents
indexed 33410 documents
indexed 33411 documents
indexed 33412 documents
indexed 33413 documents
indexed 33414 documents
indexed 33415 documents
indexed 33416 documents
indexed 33417 documents
indexed 33418 documents
indexed 33419 documents
indexed 33420 documents
indexed 33421 documents
indexed 33422 documents
indexed 33423 documents
indexed 33424 documents
indexed 33425 documents
indexed 33426 documents
indexed 33427 documents
indexed 33428 documents
indexed 33429 documents
indexed 33430 documents
indexed 33431 documents
indexed 33432 documents
indexed 33433 documents
indexed 33434 documents
indexed 33435 documents
indexed 33436 documents
indexed 33437 documents
indexed 33438 documents
indexed 33439 documents
indexed 33440 documents
indexed 33441 documents
indexed 33442 documents
indexed 33443 documents
indexed 33444 documents
indexed 33445 documents
indexed 33446 documents
indexed 33447 documents
indexed 33448 documents
indexed 33449 documents
indexed 33450 do

indexed 33753 documents
indexed 33754 documents
indexed 33755 documents
indexed 33756 documents
indexed 33757 documents
indexed 33758 documents
indexed 33759 documents
indexed 33760 documents
indexed 33761 documents
indexed 33762 documents
indexed 33763 documents
indexed 33764 documents
indexed 33765 documents
indexed 33766 documents
indexed 33767 documents
indexed 33768 documents
indexed 33769 documents
indexed 33770 documents
indexed 33771 documents
indexed 33772 documents
indexed 33773 documents
indexed 33774 documents
indexed 33775 documents
indexed 33776 documents
indexed 33777 documents
indexed 33778 documents
indexed 33779 documents
indexed 33780 documents
indexed 33781 documents
indexed 33782 documents
indexed 33783 documents
indexed 33784 documents
indexed 33785 documents
indexed 33786 documents
indexed 33787 documents
indexed 33788 documents
indexed 33789 documents
indexed 33790 documents
indexed 33791 documents
indexed 33792 documents
indexed 33793 documents
indexed 33794 do

In [ ]:
!./trec_eval/trec_eval ./gov/qrels/gov.qrels output1.txt

Upload the final output to Wattle, but **please first rename output_file to YourUID_output_q3.txt eg u1234567_output_q3.txt - FAILURE TO DO SO WILL RESULT IN -0.5 POINTS**.

### Q4: Improving the indexer: compare different ways of indexing (1 mark)

For this part, you will be asked to change the configuration of indexer (`basic_settings`) to improve the search performance.

Please look at the elastic search official document [here](https://www.elastic.co/guide/en/elasticsearch/reference/current/analysis.html) for better understanding of configuration and other options.

Note that you can check how your tokeniser tokenises your input string via the `analyze_query` function provided in the demo code.

In [11]:
# TODO: configure settings to define your own analyzer for indexing
q4_settings = {
  "mappings": {
    "doc": {
      "properties": {
        "filename": {
          "type": "keyword",
          "index": False,
        },
        "path": {
          "type": "keyword",
          "index": False,
        },
        "text": {
          "type": "text",
          "similarity": "BM25",
          "analyzer": "my_analyzer",
          "search_analyzer": "my_analyzer"
        }
      }
    }
  },
  "settings": {
    "analysis": {
      "analyzer": {
        "my_analyzer": {
          "filter": [
            "stop"
          ],
          "char_filter": [
            "html_strip"
          ],
          "type": "custom",
          "tokenizer": "lowercase"
        }
      }
    }
  }   
}
output_file2 = 'output2.txt'

In [12]:
# TODO: run this block to generate an output based on q4_settings and my_search defined above.
build_gov_index(es_conn, INDEX_NAME, DOCS_PATH, q4_settings)
read_search_write_output(search, query_path, output_file2)

index `gov` deleted
index `gov` created
indexed 1 documents
indexed 2 documents
indexed 3 documents
indexed 4 documents
indexed 5 documents
indexed 6 documents
indexed 7 documents
indexed 8 documents
indexed 9 documents
indexed 10 documents
indexed 11 documents
indexed 12 documents
indexed 13 documents
indexed 14 documents
indexed 15 documents
indexed 16 documents
indexed 17 documents
indexed 18 documents
indexed 19 documents
indexed 20 documents
indexed 21 documents
indexed 22 documents
indexed 23 documents
indexed 24 documents
indexed 25 documents
indexed 26 documents
indexed 27 documents
indexed 28 documents
indexed 29 documents
indexed 30 documents
indexed 31 documents
indexed 32 documents
indexed 33 documents
indexed 34 documents
indexed 35 documents
indexed 36 documents
indexed 37 documents
indexed 38 documents
indexed 39 documents
indexed 40 documents
indexed 41 documents
indexed 42 documents
indexed 43 documents
indexed 44 documents
indexed 45 documents
indexed 46 documents
ind

indexed 381 documents
indexed 382 documents
indexed 383 documents
indexed 384 documents
indexed 385 documents
indexed 386 documents
indexed 387 documents
indexed 388 documents
indexed 389 documents
indexed 390 documents
indexed 391 documents
indexed 392 documents
indexed 393 documents
indexed 394 documents
indexed 395 documents
indexed 396 documents
indexed 397 documents
indexed 398 documents
indexed 399 documents
indexed 400 documents
indexed 401 documents
indexed 402 documents
indexed 403 documents
indexed 404 documents
indexed 405 documents
indexed 406 documents
indexed 407 documents
indexed 408 documents
indexed 409 documents
indexed 410 documents
indexed 411 documents
indexed 412 documents
indexed 413 documents
indexed 414 documents
indexed 415 documents
indexed 416 documents
indexed 417 documents
indexed 418 documents
indexed 419 documents
indexed 420 documents
indexed 421 documents
indexed 422 documents
indexed 423 documents
indexed 424 documents
indexed 425 documents
indexed 42

indexed 758 documents
indexed 759 documents
indexed 760 documents
indexed 761 documents
indexed 762 documents
indexed 763 documents
indexed 764 documents
indexed 765 documents
indexed 766 documents
indexed 767 documents
indexed 768 documents
indexed 769 documents
indexed 770 documents
indexed 771 documents
indexed 772 documents
indexed 773 documents
indexed 774 documents
indexed 775 documents
indexed 776 documents
indexed 777 documents
indexed 778 documents
indexed 779 documents
indexed 780 documents
indexed 781 documents
indexed 782 documents
indexed 783 documents
indexed 784 documents
indexed 785 documents
indexed 786 documents
indexed 787 documents
indexed 788 documents
indexed 789 documents
indexed 790 documents
indexed 791 documents
indexed 792 documents
indexed 793 documents
indexed 794 documents
indexed 795 documents
indexed 796 documents
indexed 797 documents
indexed 798 documents
indexed 799 documents
indexed 800 documents
indexed 801 documents
indexed 802 documents
indexed 80

indexed 1128 documents
indexed 1129 documents
indexed 1130 documents
indexed 1131 documents
indexed 1132 documents
indexed 1133 documents
indexed 1134 documents
indexed 1135 documents
indexed 1136 documents
indexed 1137 documents
indexed 1138 documents
indexed 1139 documents
indexed 1140 documents
indexed 1141 documents
indexed 1142 documents
indexed 1143 documents
indexed 1144 documents
indexed 1145 documents
indexed 1146 documents
indexed 1147 documents
indexed 1148 documents
indexed 1149 documents
indexed 1150 documents
indexed 1151 documents
indexed 1152 documents
indexed 1153 documents
indexed 1154 documents
indexed 1155 documents
indexed 1156 documents
indexed 1157 documents
indexed 1158 documents
indexed 1159 documents
indexed 1160 documents
indexed 1161 documents
indexed 1162 documents
indexed 1163 documents
indexed 1164 documents
indexed 1165 documents
indexed 1166 documents
indexed 1167 documents
indexed 1168 documents
indexed 1169 documents
indexed 1170 documents
indexed 117

indexed 1485 documents
indexed 1486 documents
indexed 1487 documents
indexed 1488 documents
indexed 1489 documents
indexed 1490 documents
indexed 1491 documents
indexed 1492 documents
indexed 1493 documents
indexed 1494 documents
indexed 1495 documents
indexed 1496 documents
indexed 1497 documents
indexed 1498 documents
indexed 1499 documents
indexed 1500 documents
indexed 1501 documents
indexed 1502 documents
indexed 1503 documents
indexed 1504 documents
indexed 1505 documents
indexed 1506 documents
indexed 1507 documents
indexed 1508 documents
indexed 1509 documents
indexed 1510 documents
indexed 1511 documents
indexed 1512 documents
indexed 1513 documents
indexed 1514 documents
indexed 1515 documents
indexed 1516 documents
indexed 1517 documents
indexed 1518 documents
indexed 1519 documents
indexed 1520 documents
indexed 1521 documents
indexed 1522 documents
indexed 1523 documents
indexed 1524 documents
indexed 1525 documents
indexed 1526 documents
indexed 1527 documents
indexed 152

...

indexed 32384 documents
indexed 32385 documents
indexed 32386 documents
indexed 32387 documents
indexed 32388 documents
indexed 32389 documents
indexed 32390 documents
indexed 32391 documents
indexed 32392 documents
indexed 32393 documents
indexed 32394 documents
indexed 32395 documents
indexed 32396 documents
indexed 32397 documents
indexed 32398 documents
indexed 32399 documents
indexed 32400 documents
indexed 32401 documents
indexed 32402 documents
indexed 32403 documents
indexed 32404 documents
indexed 32405 documents
indexed 32406 documents
indexed 32407 documents
indexed 32408 documents
indexed 32409 documents
indexed 32410 documents
indexed 32411 documents
indexed 32412 documents
indexed 32413 documents
indexed 32414 documents
indexed 32415 documents
indexed 32416 documents
indexed 32417 documents
indexed 32418 documents
indexed 32419 documents
indexed 32420 documents
indexed 32421 documents
indexed 32422 documents
indexed 32423 documents
indexed 32424 documents
indexed 32425 do

indexed 32727 documents
indexed 32728 documents
indexed 32729 documents
indexed 32730 documents
indexed 32731 documents
indexed 32732 documents
indexed 32733 documents
indexed 32734 documents
indexed 32735 documents
indexed 32736 documents
indexed 32737 documents
indexed 32738 documents
indexed 32739 documents
indexed 32740 documents
indexed 32741 documents
indexed 32742 documents
indexed 32743 documents
indexed 32744 documents
indexed 32745 documents
indexed 32746 documents
indexed 32747 documents
indexed 32748 documents
indexed 32749 documents
indexed 32750 documents
indexed 32751 documents
indexed 32752 documents
indexed 32753 documents
indexed 32754 documents
indexed 32755 documents
indexed 32756 documents
indexed 32757 documents
indexed 32758 documents
indexed 32759 documents
indexed 32760 documents
indexed 32761 documents
indexed 32762 documents
indexed 32763 documents
indexed 32764 documents
indexed 32765 documents
indexed 32766 documents
indexed 32767 documents
indexed 32768 do

indexed 33069 documents
indexed 33070 documents
indexed 33071 documents
indexed 33072 documents
indexed 33073 documents
indexed 33074 documents
indexed 33075 documents
indexed 33076 documents
indexed 33077 documents
indexed 33078 documents
indexed 33079 documents
indexed 33080 documents
indexed 33081 documents
indexed 33082 documents
indexed 33083 documents
indexed 33084 documents
indexed 33085 documents
indexed 33086 documents
indexed 33087 documents
indexed 33088 documents
indexed 33089 documents
indexed 33090 documents
indexed 33091 documents
indexed 33092 documents
indexed 33093 documents
indexed 33094 documents
indexed 33095 documents
indexed 33096 documents
indexed 33097 documents
indexed 33098 documents
indexed 33099 documents
indexed 33100 documents
indexed 33101 documents
indexed 33102 documents
indexed 33103 documents
indexed 33104 documents
indexed 33105 documents
indexed 33106 documents
indexed 33107 documents
indexed 33108 documents
indexed 33109 documents
indexed 33110 do

indexed 33412 documents
indexed 33413 documents
indexed 33414 documents
indexed 33415 documents
indexed 33416 documents
indexed 33417 documents
indexed 33418 documents
indexed 33419 documents
indexed 33420 documents
indexed 33421 documents
indexed 33422 documents
indexed 33423 documents
indexed 33424 documents
indexed 33425 documents
indexed 33426 documents
indexed 33427 documents
indexed 33428 documents
indexed 33429 documents
indexed 33430 documents
indexed 33431 documents
indexed 33432 documents
indexed 33433 documents
indexed 33434 documents
indexed 33435 documents
indexed 33436 documents
indexed 33437 documents
indexed 33438 documents
indexed 33439 documents
indexed 33440 documents
indexed 33441 documents
indexed 33442 documents
indexed 33443 documents
indexed 33444 documents
indexed 33445 documents
indexed 33446 documents
indexed 33447 documents
indexed 33448 documents
indexed 33449 documents
indexed 33450 documents
indexed 33451 documents
indexed 33452 documents
indexed 33453 do

indexed 33755 documents
indexed 33756 documents
indexed 33757 documents
indexed 33758 documents
indexed 33759 documents
indexed 33760 documents
indexed 33761 documents
indexed 33762 documents
indexed 33763 documents
indexed 33764 documents
indexed 33765 documents
indexed 33766 documents
indexed 33767 documents
indexed 33768 documents
indexed 33769 documents
indexed 33770 documents
indexed 33771 documents
indexed 33772 documents
indexed 33773 documents
indexed 33774 documents
indexed 33775 documents
indexed 33776 documents
indexed 33777 documents
indexed 33778 documents
indexed 33779 documents
indexed 33780 documents
indexed 33781 documents
indexed 33782 documents
indexed 33783 documents
indexed 33784 documents
indexed 33785 documents
indexed 33786 documents
indexed 33787 documents
indexed 33788 documents
indexed 33789 documents
indexed 33790 documents
indexed 33791 documents
indexed 33792 documents
indexed 33793 documents
indexed 33794 documents
indexed 33795 documents
indexed 33796 do

In [ ]:
!./trec_eval/trec_eval ./gov/qrels/gov.qrels output2.txt

Upload the final output to Wattle, but **please first rename output_file to YourUID_output_q4.txt eg u1234567_output_q3.txt - FAILURE TO DO SO WILL RESULT IN -0.5 POINTS**.

### Q5: Tolerant retrieval: wildcard queries (1 mark)

*Elasticsearch* provides wildcard query search. You can use wildcard expressions cosisting of '*' and '?' to search.  

For this task, you can reuse the previous index, i.e., *q4_settings*. Refer to the [link](https://www.elastic.co/guide/en/elasticsearch/reference/6.3/query-dsl-wildcard-query.html) to see how to search with wildcard queries. 

For each query term from 'gov.topics', replace last two characters with any wildcard expression. For example, the first topic from 'gov.topics' is 'mining gold silver coal'. Instead, you search 'mini&ast; go?? silv&ast; co??'. 

In [2]:
q5_settings = {
  "mappings": {
    "doc": {
      "properties": {
        "filename": {
          "type": "keyword",
          "index": False,
        },
        "path": {
          "type": "keyword",
          "index": False,
        },
        "text": {
          "type": "text",
          "similarity": "BM25",
          "analyzer": "my_analyzer",
          "search_analyzer": "my_analyzer"
        }
      }
    }
  },
  "settings": {
    "analysis": {
      "analyzer": {
        "my_analyzer": {
          "filter": [
            "stop"
          ],
          "char_filter": [
            "html_strip"
          ],
          "type": "custom",
          "tokenizer": "lowercase"
        }
      }
    }
  }   
}
output_file3 = 'output3.txt'

In [1]:
def my_search(query_string, es_conn, index_name):
    words = []
    for i in query_string.split():
        words.append(i[:-2] + "**")
    str1 = ' '.join(words)
    query_string = str1
    print(query_string)
    res = es_conn.search(index = index_name,
        body = {
            "_source": [ "filename"],
            "query": {
                "query_string": {
                    "query": query_string,
                }
            }
        }
    )
    return res['hits']['hits']

In [68]:
build_gov_index(es_conn, INDEX_NAME, DOCS_PATH, q5_settings)
read_search_write_output(my_search, query_path, output_file3)

index `gov` deleted
index `gov` created
indexed 1 documents
indexed 2 documents
indexed 3 documents
indexed 4 documents
indexed 5 documents
indexed 6 documents
indexed 7 documents
indexed 8 documents
indexed 9 documents
indexed 10 documents
indexed 11 documents
indexed 12 documents
indexed 13 documents
indexed 14 documents
indexed 15 documents
indexed 16 documents
indexed 17 documents
indexed 18 documents
indexed 19 documents
indexed 20 documents
indexed 21 documents
indexed 22 documents
indexed 23 documents
indexed 24 documents
indexed 25 documents
indexed 26 documents
indexed 27 documents
indexed 28 documents
indexed 29 documents
indexed 30 documents
indexed 31 documents
indexed 32 documents
indexed 33 documents
indexed 34 documents
indexed 35 documents
indexed 36 documents
indexed 37 documents
indexed 38 documents
indexed 39 documents
indexed 40 documents
indexed 41 documents
indexed 42 documents
indexed 43 documents
indexed 44 documents
indexed 45 documents
indexed 46 documents
ind

indexed 381 documents
indexed 382 documents
indexed 383 documents
indexed 384 documents
indexed 385 documents
indexed 386 documents
indexed 387 documents
indexed 388 documents
indexed 389 documents
indexed 390 documents
indexed 391 documents
indexed 392 documents
indexed 393 documents
indexed 394 documents
indexed 395 documents
indexed 396 documents
indexed 397 documents
indexed 398 documents
indexed 399 documents
indexed 400 documents
indexed 401 documents
indexed 402 documents
indexed 403 documents
indexed 404 documents
indexed 405 documents
indexed 406 documents
indexed 407 documents
indexed 408 documents
indexed 409 documents
indexed 410 documents
indexed 411 documents
indexed 412 documents
indexed 413 documents
indexed 414 documents
indexed 415 documents
indexed 416 documents
indexed 417 documents
indexed 418 documents
indexed 419 documents
indexed 420 documents
indexed 421 documents
indexed 422 documents
indexed 423 documents
indexed 424 documents
indexed 425 documents
indexed 42

indexed 758 documents
indexed 759 documents
indexed 760 documents
indexed 761 documents
indexed 762 documents
indexed 763 documents
indexed 764 documents
indexed 765 documents
indexed 766 documents
indexed 767 documents
indexed 768 documents
indexed 769 documents
indexed 770 documents
indexed 771 documents
indexed 772 documents
indexed 773 documents
indexed 774 documents
indexed 775 documents
indexed 776 documents
indexed 777 documents
indexed 778 documents
indexed 779 documents
indexed 780 documents
indexed 781 documents
indexed 782 documents
indexed 783 documents
indexed 784 documents
indexed 785 documents
indexed 786 documents
indexed 787 documents
indexed 788 documents
indexed 789 documents
indexed 790 documents
indexed 791 documents
indexed 792 documents
indexed 793 documents
indexed 794 documents
indexed 795 documents
indexed 796 documents
indexed 797 documents
indexed 798 documents
indexed 799 documents
indexed 800 documents
indexed 801 documents
indexed 802 documents
indexed 80

indexed 1128 documents
indexed 1129 documents
indexed 1130 documents
indexed 1131 documents
indexed 1132 documents
indexed 1133 documents
indexed 1134 documents
indexed 1135 documents
indexed 1136 documents
indexed 1137 documents
indexed 1138 documents
indexed 1139 documents
indexed 1140 documents
indexed 1141 documents
indexed 1142 documents
indexed 1143 documents
indexed 1144 documents
indexed 1145 documents
indexed 1146 documents
indexed 1147 documents
indexed 1148 documents
indexed 1149 documents
indexed 1150 documents
indexed 1151 documents
indexed 1152 documents
indexed 1153 documents
indexed 1154 documents
indexed 1155 documents
indexed 1156 documents
indexed 1157 documents
indexed 1158 documents
indexed 1159 documents
indexed 1160 documents
indexed 1161 documents
indexed 1162 documents
indexed 1163 documents
indexed 1164 documents
indexed 1165 documents
indexed 1166 documents
indexed 1167 documents
indexed 1168 documents
indexed 1169 documents
indexed 1170 documents
indexed 117

indexed 1488 documents
indexed 1489 documents
indexed 1490 documents
indexed 1491 documents
indexed 1492 documents
indexed 1493 documents
indexed 1494 documents
indexed 1495 documents
indexed 1496 documents
indexed 1497 documents
indexed 1498 documents
indexed 1499 documents
indexed 1500 documents
indexed 1501 documents
indexed 1502 documents
indexed 1503 documents
indexed 1504 documents
indexed 1505 documents
indexed 1506 documents
indexed 1507 documents
indexed 1508 documents
indexed 1509 documents
indexed 1510 documents
indexed 1511 documents
indexed 1512 documents
indexed 1513 documents
indexed 1514 documents
indexed 1515 documents
indexed 1516 documents
indexed 1517 documents
indexed 1518 documents
indexed 1519 documents
indexed 1520 documents
indexed 1521 documents
indexed 1522 documents
indexed 1523 documents
indexed 1524 documents
indexed 1525 documents
indexed 1526 documents
indexed 1527 documents
indexed 1528 documents
indexed 1529 documents
indexed 1530 documents
indexed 153

...

indexed 31320 documents
indexed 31321 documents
indexed 31322 documents
indexed 31323 documents
indexed 31324 documents
indexed 31325 documents
indexed 31326 documents
indexed 31327 documents
indexed 31328 documents
indexed 31329 documents
indexed 31330 documents
indexed 31331 documents
indexed 31332 documents
indexed 31333 documents
indexed 31334 documents
indexed 31335 documents
indexed 31336 documents
indexed 31337 documents
indexed 31338 documents
indexed 31339 documents
indexed 31340 documents
indexed 31341 documents
indexed 31342 documents
indexed 31343 documents
indexed 31344 documents
indexed 31345 documents
indexed 31346 documents
indexed 31347 documents
indexed 31348 documents
indexed 31349 documents
indexed 31350 documents
indexed 31351 documents
indexed 31352 documents
indexed 31353 documents
indexed 31354 documents
indexed 31355 documents
indexed 31356 documents
indexed 31357 documents
indexed 31358 documents
indexed 31359 documents
indexed 31360 documents
indexed 31361 do

indexed 31662 documents
indexed 31663 documents
indexed 31664 documents
indexed 31665 documents
indexed 31666 documents
indexed 31667 documents
indexed 31668 documents
indexed 31669 documents
indexed 31670 documents
indexed 31671 documents
indexed 31672 documents
indexed 31673 documents
indexed 31674 documents
indexed 31675 documents
indexed 31676 documents
indexed 31677 documents
indexed 31678 documents
indexed 31679 documents
indexed 31680 documents
indexed 31681 documents
indexed 31682 documents
indexed 31683 documents
indexed 31684 documents
indexed 31685 documents
indexed 31686 documents
indexed 31687 documents
indexed 31688 documents
indexed 31689 documents
indexed 31690 documents
indexed 31691 documents
indexed 31692 documents
indexed 31693 documents
indexed 31694 documents
indexed 31695 documents
indexed 31696 documents
indexed 31697 documents
indexed 31698 documents
indexed 31699 documents
indexed 31700 documents
indexed 31701 documents
indexed 31702 documents
indexed 31703 do

indexed 32004 documents
indexed 32005 documents
indexed 32006 documents
indexed 32007 documents
indexed 32008 documents
indexed 32009 documents
indexed 32010 documents
indexed 32011 documents
indexed 32012 documents
indexed 32013 documents
indexed 32014 documents
indexed 32015 documents
indexed 32016 documents
indexed 32017 documents
indexed 32018 documents
indexed 32019 documents
indexed 32020 documents
indexed 32021 documents
indexed 32022 documents
indexed 32023 documents
indexed 32024 documents
indexed 32025 documents
indexed 32026 documents
indexed 32027 documents
indexed 32028 documents
indexed 32029 documents
indexed 32030 documents
indexed 32031 documents
indexed 32032 documents
indexed 32033 documents
indexed 32034 documents
indexed 32035 documents
indexed 32036 documents
indexed 32037 documents
indexed 32038 documents
indexed 32039 documents
indexed 32040 documents
indexed 32041 documents
indexed 32042 documents
indexed 32043 documents
indexed 32044 documents
indexed 32045 do

indexed 32347 documents
indexed 32348 documents
indexed 32349 documents
indexed 32350 documents
indexed 32351 documents
indexed 32352 documents
indexed 32353 documents
indexed 32354 documents
indexed 32355 documents
indexed 32356 documents
indexed 32357 documents
indexed 32358 documents
indexed 32359 documents
indexed 32360 documents
indexed 32361 documents
indexed 32362 documents
indexed 32363 documents
indexed 32364 documents
indexed 32365 documents
indexed 32366 documents
indexed 32367 documents
indexed 32368 documents
indexed 32369 documents
indexed 32370 documents
indexed 32371 documents
indexed 32372 documents
indexed 32373 documents
indexed 32374 documents
indexed 32375 documents
indexed 32376 documents
indexed 32377 documents
indexed 32378 documents
indexed 32379 documents
indexed 32380 documents
indexed 32381 documents
indexed 32382 documents
indexed 32383 documents
indexed 32384 documents
indexed 32385 documents
indexed 32386 documents
indexed 32387 documents
indexed 32388 do

ConnectionTimeout: ConnectionTimeout caused by - ReadTimeoutError(HTTPConnectionPool(host='localhost', port=9200): Read timed out. (read timeout=10))

mini* go* silv* co*
juveni* delinquen*
wirele* communicatio*
physic* therapis*
cott* indust*
genealo* search*
Physic* Fitne*
Agricultur* biotechnolo*
Emergen* a* disast* preparedne* assistan*
Shipwrec*
Cybercrim* intern* frau* a* cyb* fra*
Veteran* Benefi*
A* B* Safe*
Nucle* pow* plan*
Ear* Childho* Educati*
deafne* * childr*
wildli* conservati*
fo* safe*
Litera*
arct* explorati*
glob* warmi*
co* collecti*
weath* hazar* a* extrem*
Nation* Publ* Radio\/*
Electr* Automobil*
homelessne*
fore* fir*
Ozo* lay*
trains\/railroa*
robo*
anthr*


In [56]:
!./trec_eval/trec_eval ./gov/qrels/gov.qrels output3.txt

'.' is not recognized as an internal or external command,
operable program or batch file.


## Written component (Q6 - Q9), 6 marks

Answer the following questions based on your implementation of Questions 1-5:

### Q6 (1.5 marks): What changs did you make to the search similarity to improve the performance of the system? Why do you think it improved the performance?

(provide answers below using bullet points with 2~3 items)

 - The change I made to the search similarity to improve the performance is I replaced boolean similarity with the BM25 similarity(which is tdfif basically)
 
 
 - This change of search similarity has improved the accuracy from 0.08 to 0.1567 percent. This change made improved the performance because the boolean retreival only helps us to know that the word is present or not. But BM25, tells about the significance of the word as well as the document due to which is ranked accordingly. So, the top 10 documents that we get in BM25 are the most the relevant documents whereas the boolean retreival takes 10 documents which have the query not in an order.So, this will automatically increase the accuracy.

### Q7 (1.5 marks): What changes did you make to the indexer to improve the performance of the system? Why do you think it improved the performance?

(provide answer below using bullet points with 2~3 items (Check [this](https://sourceforge.net/p/jupiter/wiki/markdown_syntax/#md_ex_lists) if you are not familiar with markdown syntax))

 - The changes I made to the indexer to improve the performance of the system is I changed the similarity to BM25 and changed the tokenizer from the whitespace to lowercase.
 
 
 - This change of search similarity has improved the accuracy. This change made improved the performance because the boolean retreival only helps us to know that the word is present or not. But BM25, tells about the significance of the word as well as the document due to which is ranked accordingly. So, the top 10 documents that we get in BM25 are the most the relevant documents whereas the boolean retreival takes 10 documents which have the query not in an order.So, this will automatically increase the accuracy.

-  The change I made in the tokenizer from the whitespace to lowercase is because If the query is in capital letters and that word in the document is present but is in small letters.Due to whitespace tokenizer, It doesn't take some documents in account due to this reason. So, If we use the lowercase tokenizer, then the query as well as the document would be in lowercase and it will give more precise result and it will also overcome the problem faced byt the whitespace tokenizer. For the evidenece, we can also see that the output as the 'output1.txt' which has used whitespace tokenizer has 300 documents whereas there are 310 documents in the 'output2.txt' on which the lowercase tokenizer was applied. We can also see from the accuracy that the increased from 15.67 to 27.42 percent. 

### Q8 (1.5 marks): Apart from Precision@10, what other metrics can be used to measure the performance of the developed IR system for the government document collection? Provide two metrics and explain why they would be suited for this particular government IR system.

(provide answers below using bullet points with 2~3 items)

 - Reciprocal Rank

### Q9 (1.5 marks): How do wildcard queries affect performance of the retrieval in terms of measures you answered for Q8? Also provide some situations when wildcard queries are useful. 

The wildcards queries will affect the performance. The performance will decrease for this case because over here we are quering the wildcards will make the changes to queries we are searhing for because in wildcards queries, lets say if we take 'ray' then it will search for ra*, r*a, *ay etc which is not relevant as we just want to search for ray. So, at the end, it will not give many relevant documents which will decrease the accuracy. 

Wildcards can be are useful when we want to find the query something like we have to find all the words in the document ending with the mon.Then in this, it will search for *mon and now it will give the relevant documents.

**Academic Misconduct Policy**: All submitted written work and code must be your own (except for any provided starter code, of course) – submitting work other than your own will lead to both a failure on the assignment and a referral of the case to the ANU academic misconduct review procedures: ANU Academic Misconduct Procedures